# Converter
## pyLASCA

(c) Sebastian Malkusch 2019

In [1]:
import numpy as np
import plotly.tools as tls
import plotly.express as px
import plotly.graph_objects as go
from plotly.offline import iplot
from plotly.subplots import make_subplots
from pyLASCA.gui.converterWidgets import ConverterWidgets
from pyLASCA.source.fileNames import FileNames
from pyLASCA.source.textDocumentConverter import TextDocumentConverter
widgets = ConverterWidgets()
fileNames = FileNames()
textDocument = TextDocumentConverter()

PyLascaWidgets initialized


## Load Text File
needs to be event driven

In [2]:
display(widgets.pathText, widgets.pathButton)

Text(value='', description='path to file', placeholder='enter a string', style=DescriptionStyle(description_wi…

Button(description='browse', icon='check', style=ButtonStyle(), tooltip='Click me')

## Convert Data

In [3]:
display(widgets.convertButton)

def runConversion(event):
    if(widgets.fileName):
        fileNames.fileName = widgets.fileName
        fileNames.splitFileName()
        textDocument.fileName = fileNames.fileName
        textDocument.readTextDocument(fileName = fileNames.fileName)
        widgets.frameSelector.max = textDocument.frames-1
        widgets.frameSelector.value = 0
        widgets.clearOutput()
        display(widgets.convertButton)
        print(textDocument)
        
        
    
widgets.convertButton.on_click(runConversion)

Button(description='convert', icon='check', style=ButtonStyle(), tooltip='Click me')

TextDocument dimensions:
x: 752
y: 580
frames: 3



## Visualize

In [4]:
display(widgets.frameSelector)

def updateImage(event):
    widgets.clearOutput()
    display(widgets.frameSelector)
    if (textDocument.frames > 0):
        frame = textDocument.frame(frame = widgets.frameSelector.value)
        fig_image = go.Heatmap(z = frame.tolist(),
                               colorscale='Viridis',
                               colorbar=dict(title='intensity'),)
        df_hist = textDocument.histFrame(frame = widgets.frameSelector.value)
        fig_hist = go.Bar(x=df_hist["intensity"],y=df_hist["frequency"])
        fig = make_subplots(rows=1, cols=2, subplot_titles=("Heatmap", "Histogram"))
        fig.add_trace(fig_image, row=1, col=1)
        fig.add_trace(fig_hist, row=1, col=2)
        
        fig.update_xaxes(title_text="x [pxl]", row=1, col=1)
        fig.update_yaxes(title_text="y [pxl]", row=1, col=1)
        fig.update_xaxes(title_text="intensity [a.u.]", range=[0, 255], row=1, col=2)
        fig.update_yaxes(title_text="frequency", row=1, col=2)
        fig.update_layout(
            title = str("Frame %i" %(widgets.frameSelector.value)),
            yaxis = dict(
                scaleanchor = "x",
                scaleratio = float(textDocument.x)/float(textDocument.y))
        )
        iplot(fig)
        
        

widgets.frameSelector.observe(updateImage);

BoundedIntText(value=1, description='channel', max=2, style=DescriptionStyle(description_width='initial'))

## Save Image
needs to be event driven

In [5]:
display(widgets.saveButton)

def saveImage(event):
    widgets.clearOutput()
    display(widgets.saveButton)
    if (textDocument.frames > 0):
        n = widgets.frameSelector.value
        fileNames.supplementalInformation = str("frame-%i" %(n))
        fileNames.suffix = "tiff"
        fileNames.updateDateString()
        fileNames.mergeFileName()
        textDocument.writeFrameToImage(frame = n, fileName = fileNames.outFileName)
        
widgets.saveButton.on_click(saveImage)

Button(description='save', icon='check', style=ButtonStyle(), tooltip='Click me')